This notebook assumes you have already followed the steps in `README.md`. If not, do that first!

In [43]:
import os
import matplotlib.pyplot as plt
import numpy as np
import tensorflow as tf
from pathlib import Path
import tifffile

In [44]:
!ls

11_band_data	  Explore Images.ipynb	README.md	   tensorflow_train.py
data		  extra_data.csv	requirements.txt   train.py
download_data.sh  extra_data key.pdf	Save_Images.ipynb  Untitled.ipynb


In [6]:
tf.enable_eager_execution()

In [154]:
dirlist = lambda di: [os.path.join(di, file) for file in os.listdir(di) if 'part-' in file]
training_files = dirlist('data/train/')

def parse_visual(data):
    dataset = tf.data.TFRecordDataset(data)
    # pattern for one part file
    # dataset = tf.data.TFRecordDataset('part-r-00099')
    iterator = dataset.make_one_shot_iterator()

    features = {
        'B1': tf.FixedLenFeature([], tf.string),
        'B2': tf.FixedLenFeature([], tf.string),
        'B3': tf.FixedLenFeature([], tf.string),
        'B4': tf.FixedLenFeature([], tf.string),
        'B5': tf.FixedLenFeature([], tf.string),
        'B6': tf.FixedLenFeature([], tf.string),
        'B7': tf.FixedLenFeature([], tf.string),
        'B8': tf.FixedLenFeature([], tf.string),
        'B9': tf.FixedLenFeature([], tf.string),
        'B10': tf.FixedLenFeature([], tf.string),
        'B11': tf.FixedLenFeature([], tf.string),
        'label': tf.FixedLenFeature([], tf.int64),
    }

    parsed_examples = [tf.parse_single_example(data, features) for data in iterator]
    return parsed_examples

parsed_examples = parse_visual(training_files)

In [41]:
def get_bands_from_example(parsed_example, intensify=True):
    rgbArray = np.zeros((65,65,11), 'uint8')
    for i, band in enumerate(['B'+str(i) for i in range(11,0,-1)]):
        band_data = np.frombuffer(parsed_example[band].numpy(), dtype=np.uint8)
        band_data = band_data.reshape(65, 65)
        if intensify:
            band_data = band_data/np.max(band_data)*255
        else:
            band_data = band_data*255
        rgbArray[..., i] = band_data
        
    label = tf.cast(parsed_example['label'], tf.int32).numpy()
        
    return rgbArray, label

In [21]:
def get_img_from_example(parsed_example, intensify=True):
    rgbArray = np.zeros((65,65,3), 'uint8')
    for i, band in enumerate(['B4', 'B3', 'B2']):
        band_data = np.frombuffer(parsed_example[band].numpy(), dtype=np.uint8)
        band_data = band_data.reshape(65, 65)
        if intensify:
            band_data = band_data/np.max(band_data)*255
        else:
            band_data = band_data*255
        rgbArray[..., i] = band_data
        
    label = tf.cast(parsed_example['label'], tf.int32).numpy()
        
    return rgbArray, label

In [155]:
#fig=plt.figure(figsize=(20, 30), dpi= 80, facecolor='w', edgecolor='k')
cur=Path.cwd()
rgb_dest=cur/'data'/'train'
band_dest=cur/'11_band_data'/'train'
for i in range(0,len(parsed_examples)):
    img,label=get_img_from_example(parsed_examples[i])
    band_img,_=get_bands_from_example(parsed_examples[i])
    band_img=band_img.transpose([2,0,1])
    
    rgb_name=rgb_dest/str(label)/('img_'+str(i)+'.tiff')
    band_name=band_dest/str(label)/('img_'+str(i)+'.tiff')
    
    tifffile.imsave(band_name, band_img)
    plt.imsave(rgb_name,img)
    print(i)
    #plt.subplot(5, 5, i)
    #img, label = img, label = get_img_from_example(parsed_examples[i+7])
    #plt.imshow(img).axes.get_xaxis().set_visible(False)
    #plt.imshow(img).axes.get_yaxis().set_visible(False)
    #plt.title(str(label))

#fig.show()

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91


/home/ubuntu/anaconda3/envs/fastai/lib/python3.7/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in true_divide
  import sys


92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
306
307
308
309
310
311
312
313
314
315
316
317
318
319
320
321
322
323
324
325
326
327
328
329
330
331
332
333
334
335
336
337
338
339
340
341
342
343


1932
1933
1934
1935
1936
1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973
1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989
1990
1991
1992
1993
1994
1995
1996
1997
1998
1999
2000
2001
2002
2003
2004
2005
2006
2007
2008
2009
2010
2011
2012
2013
2014
2015
2016
2017
2018
2019
2020
2021
2022
2023
2024
2025
2026
2027
2028
2029
2030
2031
2032
2033
2034
2035
2036
2037
2038
2039
2040
2041
2042
2043
2044
2045
2046
2047
2048
2049
2050
2051
2052
2053
2054
2055
2056
2057
2058
2059
2060
2061
2062
2063
2064
2065
2066
2067
2068
2069
2070
2071
2072
2073
2074
2075
2076
2077
2078
2079
2080
2081
2082
2083
2084
2085
2086
2087
2088
2089
2090
2091
2092
2093
2094
2095
2096
2097
2098
2099
2100
2101
2102
2103
2104
2105
2106
2107
2108
2109
2110
2111
2112
2113
2114
2115
2116
2117
2118
2119
2120
2121
2122
2123
2124
2125
2126
2127
2128
2129
2130
2131


3588
3589
3590
3591
3592
3593
3594
3595
3596
3597
3598
3599
3600
3601
3602
3603
3604
3605
3606
3607
3608
3609
3610
3611
3612
3613
3614
3615
3616
3617
3618
3619
3620
3621
3622
3623
3624
3625
3626
3627
3628
3629
3630
3631
3632
3633
3634
3635
3636
3637
3638
3639
3640
3641
3642
3643
3644
3645
3646
3647
3648
3649
3650
3651
3652
3653
3654
3655
3656
3657
3658
3659
3660
3661
3662
3663
3664
3665
3666
3667
3668
3669
3670
3671
3672
3673
3674
3675
3676
3677
3678
3679
3680
3681
3682
3683
3684
3685
3686
3687
3688
3689
3690
3691
3692
3693
3694
3695
3696
3697
3698
3699
3700
3701
3702
3703
3704
3705
3706
3707
3708
3709
3710
3711
3712
3713
3714
3715
3716
3717
3718
3719
3720
3721
3722
3723
3724
3725
3726
3727
3728
3729
3730
3731
3732
3733
3734
3735
3736
3737
3738
3739
3740
3741
3742
3743
3744
3745
3746
3747
3748
3749
3750
3751
3752
3753
3754
3755
3756
3757
3758
3759
3760
3761
3762
3763
3764
3765
3766
3767
3768
3769
3770
3771
3772
3773
3774
3775
3776
3777
3778
3779
3780
3781
3782
3783
3784
3785
3786
3787


...

80603
80604
80605
80606
80607
80608
80609
80610
80611
80612
80613
80614
80615
80616
80617
80618
80619
80620
80621
80622
80623
80624
80625
80626
80627
80628
80629
80630
80631
80632
80633
80634
80635
80636
80637
80638
80639
80640
80641
80642
80643
80644
80645
80646
80647
80648
80649
80650
80651
80652
80653
80654
80655
80656
80657
80658
80659
80660
80661
80662
80663
80664
80665
80666
80667
80668
80669
80670
80671
80672
80673
80674
80675
80676
80677
80678
80679
80680
80681
80682
80683
80684
80685
80686
80687
80688
80689
80690
80691
80692
80693
80694
80695
80696
80697
80698
80699
80700
80701
80702
80703
80704
80705
80706
80707
80708
80709
80710
80711
80712
80713
80714
80715
80716
80717
80718
80719
80720
80721
80722
80723
80724
80725
80726
80727
80728
80729
80730
80731
80732
80733
80734
80735
80736
80737
80738
80739
80740
80741
80742
80743
80744
80745
80746
80747
80748
80749
80750
80751
80752
80753
80754
80755
80756
80757
80758
80759
80760
80761
80762
80763
80764
80765
80766
80767
80768
8076

81983
81984
81985
81986
81987
81988
81989
81990
81991
81992
81993
81994
81995
81996
81997
81998
81999
82000
82001
82002
82003
82004
82005
82006
82007
82008
82009
82010
82011
82012
82013
82014
82015
82016
82017
82018
82019
82020
82021
82022
82023
82024
82025
82026
82027
82028
82029
82030
82031
82032
82033
82034
82035
82036
82037
82038
82039
82040
82041
82042
82043
82044
82045
82046
82047
82048
82049
82050
82051
82052
82053
82054
82055
82056
82057
82058
82059
82060
82061
82062
82063
82064
82065
82066
82067
82068
82069
82070
82071
82072
82073
82074
82075
82076
82077
82078
82079
82080
82081
82082
82083
82084
82085
82086
82087
82088
82089
82090
82091
82092
82093
82094
82095
82096
82097
82098
82099
82100
82101
82102
82103
82104
82105
82106
82107
82108
82109
82110
82111
82112
82113
82114
82115
82116
82117
82118
82119
82120
82121
82122
82123
82124
82125
82126
82127
82128
82129
82130
82131
82132
82133
82134
82135
82136
82137
82138
82139
82140
82141
82142
82143
82144
82145
82146
82147
82148
8214

83363
83364
83365
83366
83367
83368
83369
83370
83371
83372
83373
83374
83375
83376
83377
83378
83379
83380
83381
83382
83383
83384
83385
83386
83387
83388
83389
83390
83391
83392
83393
83394
83395
83396
83397
83398
83399
83400
83401
83402
83403
83404
83405
83406
83407
83408
83409
83410
83411
83412
83413
83414
83415
83416
83417
83418
83419
83420
83421
83422
83423
83424
83425
83426
83427
83428
83429
83430
83431
83432
83433
83434
83435
83436
83437
83438
83439
83440
83441
83442
83443
83444
83445
83446
83447
83448
83449
83450
83451
83452
83453
83454
83455
83456
83457
83458
83459
83460
83461
83462
83463
83464
83465
83466
83467
83468
83469
83470
83471
83472
83473
83474
83475
83476
83477
83478
83479
83480
83481
83482
83483
83484
83485
83486
83487
83488
83489
83490
83491
83492
83493
83494
83495
83496
83497
83498
83499
83500
83501
83502
83503
83504
83505
83506
83507
83508
83509
83510
83511
83512
83513
83514
83515
83516
83517
83518
83519
83520
83521
83522
83523
83524
83525
83526
83527
83528
8352

84740
84741
84742
84743
84744
84745
84746
84747
84748
84749
84750
84751
84752
84753
84754
84755
84756
84757
84758
84759
84760
84761
84762
84763
84764
84765
84766
84767
84768
84769
84770
84771
84772
84773
84774
84775
84776
84777
84778
84779
84780
84781
84782
84783
84784
84785
84786
84787
84788
84789
84790
84791
84792
84793
84794
84795
84796
84797
84798
84799
84800
84801
84802
84803
84804
84805
84806
84807
84808
84809
84810
84811
84812
84813
84814
84815
84816
84817
84818
84819
84820
84821
84822
84823
84824
84825
84826
84827
84828
84829
84830
84831
84832
84833
84834
84835
84836
84837
84838
84839
84840
84841
84842
84843
84844
84845
84846
84847
84848
84849
84850
84851
84852
84853
84854
84855
84856
84857
84858
84859
84860
84861
84862
84863
84864
84865
84866
84867
84868
84869
84870
84871
84872
84873
84874
84875
84876
84877
84878
84879
84880
84881
84882
84883
84884
84885
84886
84887
84888
84889
84890
84891
84892
84893
84894
84895
84896
84897
84898
84899
84900
84901
84902
84903
84904
84905
8490

86120
86121
86122
86123
86124
86125
86126
86127
86128
86129
86130
86131
86132
86133
86134
86135
86136
86137
86138
86139
86140
86141
86142
86143
86144
86145
86146
86147
86148
86149
86150
86151
86152
86153
86154
86155
86156
86157
86158
86159
86160
86161
86162
86163
86164
86165
86166
86167
86168
86169
86170
86171
86172
86173
86174
86175
86176
86177
86178
86179
86180
86181
86182
86183
86184
86185
86186
86187
86188
86189
86190
86191
86192
86193
86194
86195
86196
86197
86198
86199
86200
86201
86202
86203
86204
86205
86206
86207
86208
86209
86210
86211
86212
86213
86214
86215
86216
86217
86218
86219
86220
86221
86222
86223
86224
86225
86226
86227
86228
86229
86230
86231
86232
86233
86234
86235
86236
86237
86238
86239
86240
86241
86242
86243
86244
86245
86246
86247
86248
86249
86250
86251
86252
86253
86254
86255
86256
86257
86258
86259
86260
86261
86262
86263
86264
86265
86266
86267
86268
86269
86270
86271
86272
86273
86274
86275
86276
86277
86278
86279
86280
86281
86282
86283
86284
86285
8628

In [156]:
!

11_band_data	  Explore Images.ipynb	README.md	   tensorflow_train.py
data		  extra_data.csv	requirements.txt   train.py
download_data.sh  extra_data key.pdf	Save_Images.ipynb  Untitled.ipynb


In [157]:
import csv

In [162]:
with open('label.csv',mode='w') as csv_f:
    for label in band_dest.glob('*'):
        for img in label.rglob('*'):
            label_writer = csv.writer(csv_f, delimiter=',', quotechar='"', quoting=csv.QUOTE_MINIMAL)
            label_writer.writerow([str(img.name),str(label.stem)])
            print([str(img.name),str(label.stem)])

['img_13061.tiff', '1']
['img_19104.tiff', '1']
['img_22738.tiff', '1']
['img_84618.tiff', '1']
['img_33129.tiff', '1']
['img_34315.tiff', '1']
['img_30460.tiff', '1']
['img_84896.tiff', '1']
['img_66906.tiff', '1']
['img_42995.tiff', '1']
['img_57563.tiff', '1']
['img_70277.tiff', '1']
['img_5044.tiff', '1']
['img_27087.tiff', '1']
['img_24485.tiff', '1']
['img_61493.tiff', '1']
['img_55363.tiff', '1']
['img_29864.tiff', '1']
['img_36447.tiff', '1']
['img_67313.tiff', '1']
['img_83721.tiff', '1']
['img_8522.tiff', '1']
['img_54203.tiff', '1']
['img_61846.tiff', '1']
['img_79533.tiff', '1']
['img_84933.tiff', '1']
['img_55654.tiff', '1']
['img_25773.tiff', '1']
['img_67714.tiff', '1']
['img_82565.tiff', '1']
['img_67802.tiff', '1']
['img_593.tiff', '1']
['img_27355.tiff', '1']
['img_66650.tiff', '1']
['img_1078.tiff', '1']
['img_41024.tiff', '1']
['img_31532.tiff', '1']
['img_16114.tiff', '1']
['img_45221.tiff', '1']
['img_72687.tiff', '1']
['img_81428.tiff', '1']
['img_60075.tiff', '1

['img_53415.tiff', '1']
['img_24339.tiff', '1']
['img_14106.tiff', '1']
['img_85042.tiff', '1']
['img_22197.tiff', '1']
['img_2466.tiff', '1']
['img_51701.tiff', '1']
['img_40512.tiff', '1']
['img_63704.tiff', '1']
['img_39394.tiff', '1']
['img_25557.tiff', '1']
['img_33245.tiff', '1']
['img_54444.tiff', '1']
['img_52397.tiff', '1']
['img_17481.tiff', '1']
['img_53488.tiff', '1']
['img_14841.tiff', '1']
['img_62429.tiff', '1']
['img_82157.tiff', '1']
['img_52324.tiff', '1']
['img_69315.tiff', '1']
['img_26984.tiff', '1']
['img_46502.tiff', '1']
['img_58619.tiff', '1']
['img_50452.tiff', '1']
['img_82615.tiff', '1']
['img_38723.tiff', '1']
['img_15202.tiff', '1']
['img_85343.tiff', '1']
['img_70535.tiff', '1']
['img_54886.tiff', '1']
['img_59524.tiff', '1']
['img_50529.tiff', '1']
['img_10675.tiff', '1']
['img_53539.tiff', '1']
['img_5905.tiff', '1']
['img_79106.tiff', '1']
['img_43259.tiff', '1']
['img_37261.tiff', '1']
['img_21085.tiff', '1']
['img_83605.tiff', '1']
['img_83283.tiff',

['img_70017.tiff', '1']
['img_15112.tiff', '1']
['img_79551.tiff', '1']
['img_73096.tiff', '1']
['img_14445.tiff', '1']
['img_75273.tiff', '1']
['img_1749.tiff', '1']
['img_33295.tiff', '1']
['img_39463.tiff', '1']
['img_13336.tiff', '1']
['img_52965.tiff', '1']
['img_41991.tiff', '1']
['img_20666.tiff', '1']
['img_40777.tiff', '1']
['img_39060.tiff', '1']
['img_3736.tiff', '1']
['img_60690.tiff', '1']
['img_71279.tiff', '1']
['img_73752.tiff', '1']
['img_12544.tiff', '1']
['img_27304.tiff', '1']
['img_65077.tiff', '1']
['img_30457.tiff', '1']
['img_11608.tiff', '1']
['img_27670.tiff', '1']
['img_75093.tiff', '1']
['img_44331.tiff', '1']
['img_19092.tiff', '1']
['img_5972.tiff', '1']
['img_13037.tiff', '1']
['img_17281.tiff', '1']
['img_59015.tiff', '1']
['img_54449.tiff', '1']
['img_27692.tiff', '1']
['img_1209.tiff', '1']
['img_83790.tiff', '1']
['img_58356.tiff', '1']
['img_31472.tiff', '1']
['img_25269.tiff', '1']
['img_69810.tiff', '1']
['img_78966.tiff', '1']
['img_69416.tiff', '

['img_24163.tiff', '1']
['img_14976.tiff', '1']
['img_14724.tiff', '1']
['img_25240.tiff', '1']
['img_38571.tiff', '1']
['img_1106.tiff', '1']
['img_32774.tiff', '1']
['img_42813.tiff', '1']
['img_59673.tiff', '1']
['img_26579.tiff', '1']
['img_44915.tiff', '1']
['img_21047.tiff', '1']
['img_8048.tiff', '1']
['img_85852.tiff', '1']
['img_74104.tiff', '1']
['img_13883.tiff', '1']
['img_57260.tiff', '1']
['img_57893.tiff', '1']
['img_45261.tiff', '1']
['img_13941.tiff', '1']
['img_5171.tiff', '1']
['img_66514.tiff', '1']
['img_15897.tiff', '1']
['img_55590.tiff', '1']
['img_25344.tiff', '1']
['img_59991.tiff', '1']
['img_41467.tiff', '1']
['img_12620.tiff', '1']
['img_66581.tiff', '1']
['img_82137.tiff', '1']
['img_27541.tiff', '1']
['img_35730.tiff', '1']
['img_12612.tiff', '1']
['img_23662.tiff', '1']
['img_31875.tiff', '1']
['img_2712.tiff', '1']
['img_7898.tiff', '1']
['img_46061.tiff', '1']
['img_77585.tiff', '1']
['img_7708.tiff', '1']
['img_44420.tiff', '1']
['img_68113.tiff', '1'

['img_61156.tiff', '1']
['img_48637.tiff', '1']
['img_86111.tiff', '1']
['img_85302.tiff', '1']
['img_64617.tiff', '1']
['img_43104.tiff', '1']
['img_6960.tiff', '1']
['img_37826.tiff', '1']
['img_55365.tiff', '1']
['img_12316.tiff', '1']
['img_15134.tiff', '1']
['img_50148.tiff', '1']
['img_66946.tiff', '1']
['img_5037.tiff', '1']
['img_75621.tiff', '1']
['img_63324.tiff', '1']
['img_46031.tiff', '1']
['img_1986.tiff', '1']
['img_83942.tiff', '1']
['img_4823.tiff', '1']
['img_9822.tiff', '1']
['img_47110.tiff', '1']
['img_10943.tiff', '1']
['img_118.tiff', '1']
['img_14060.tiff', '1']
['img_72251.tiff', '1']
['img_82202.tiff', '1']
['img_54372.tiff', '1']
['img_46198.tiff', '1']
['img_13174.tiff', '1']
['img_58790.tiff', '1']
['img_84546.tiff', '1']
['img_45080.tiff', '1']
['img_25813.tiff', '1']
['img_37526.tiff', '1']
['img_29729.tiff', '1']
['img_24258.tiff', '1']
['img_66367.tiff', '1']
['img_79340.tiff', '1']
['img_63667.tiff', '1']
['img_17853.tiff', '1']
['img_85962.tiff', '1']

...

['img_58324.tiff', '2']
['img_46922.tiff', '2']
['img_51679.tiff', '2']
['img_29055.tiff', '2']
['img_73149.tiff', '2']
['img_76750.tiff', '2']
['img_27962.tiff', '2']
['img_47396.tiff', '2']
['img_64137.tiff', '2']
['img_51889.tiff', '2']
['img_8802.tiff', '2']
['img_11243.tiff', '2']
['img_27522.tiff', '2']
['img_82988.tiff', '2']
['img_28340.tiff', '2']
['img_51593.tiff', '2']
['img_81224.tiff', '2']
['img_21011.tiff', '2']
['img_49086.tiff', '2']
['img_57485.tiff', '2']
['img_11478.tiff', '2']
['img_51347.tiff', '2']
['img_47983.tiff', '2']
['img_86212.tiff', '2']
['img_43205.tiff', '2']
['img_10319.tiff', '2']
['img_21989.tiff', '2']
['img_15856.tiff', '2']
['img_10808.tiff', '2']
['img_44841.tiff', '2']
['img_33173.tiff', '2']
['img_41622.tiff', '2']
['img_2421.tiff', '2']
['img_31833.tiff', '2']
['img_50426.tiff', '2']
['img_51221.tiff', '2']
['img_78048.tiff', '2']
['img_84502.tiff', '2']
['img_75831.tiff', '2']
['img_18407.tiff', '2']
['img_22050.tiff', '2']
['img_12839.tiff',

['img_26236.tiff', '2']
['img_34923.tiff', '2']
['img_6611.tiff', '2']
['img_17008.tiff', '2']
['img_35574.tiff', '2']
['img_581.tiff', '2']
['img_70879.tiff', '2']
['img_60081.tiff', '2']
['img_80500.tiff', '2']
['img_60756.tiff', '2']
['img_79195.tiff', '2']
['img_12506.tiff', '2']
['img_7087.tiff', '2']
['img_12454.tiff', '2']
['img_71668.tiff', '2']
['img_31050.tiff', '2']
['img_13274.tiff', '2']
['img_45432.tiff', '2']
['img_3291.tiff', '2']
['img_72100.tiff', '2']
['img_9519.tiff', '2']
['img_17641.tiff', '2']
['img_14390.tiff', '2']
['img_12322.tiff', '2']
['img_36844.tiff', '2']
['img_84403.tiff', '2']
['img_19384.tiff', '2']
['img_53896.tiff', '2']
['img_81219.tiff', '2']
['img_44546.tiff', '2']
['img_41154.tiff', '2']
['img_47342.tiff', '2']
['img_57478.tiff', '2']
['img_58606.tiff', '2']
['img_38972.tiff', '2']
['img_48257.tiff', '2']
['img_30409.tiff', '2']
['img_23165.tiff', '2']
['img_42375.tiff', '2']
['img_54513.tiff', '2']
['img_19974.tiff', '2']
['img_42112.tiff', '2'

['img_41516.tiff', '3']
['img_37921.tiff', '3']
['img_69474.tiff', '3']
['img_39738.tiff', '3']
['img_84247.tiff', '3']
['img_23173.tiff', '3']
['img_71621.tiff', '3']
['img_23838.tiff', '3']
['img_74570.tiff', '3']
['img_16129.tiff', '3']
['img_23527.tiff', '3']
['img_48919.tiff', '3']
['img_53689.tiff', '3']
['img_178.tiff', '3']
['img_69537.tiff', '3']
['img_43167.tiff', '3']
['img_14169.tiff', '3']
['img_25371.tiff', '3']
['img_1745.tiff', '3']
['img_74976.tiff', '3']
['img_33093.tiff', '3']
['img_32864.tiff', '3']
['img_30366.tiff', '3']
['img_5088.tiff', '3']
['img_7058.tiff', '3']
['img_78693.tiff', '3']
['img_51752.tiff', '3']
['img_69008.tiff', '3']
['img_84596.tiff', '3']
['img_11342.tiff', '3']
['img_70864.tiff', '3']
['img_47688.tiff', '3']
['img_25944.tiff', '3']
['img_84845.tiff', '3']
['img_26745.tiff', '3']
['img_28702.tiff', '3']
['img_69907.tiff', '3']
['img_23352.tiff', '3']
['img_37460.tiff', '3']
['img_14510.tiff', '3']
['img_21661.tiff', '3']
['img_53886.tiff', '3

['img_66743.tiff', '3']
['img_56919.tiff', '3']
['img_10709.tiff', '3']
['img_64452.tiff', '3']
['img_61195.tiff', '3']
['img_79650.tiff', '3']
['img_26169.tiff', '3']
['img_82427.tiff', '3']
['img_64386.tiff', '3']
['img_41668.tiff', '3']
['img_3635.tiff', '3']
['img_61619.tiff', '3']
['img_62037.tiff', '3']
['img_45302.tiff', '3']
['img_33065.tiff', '3']
['img_68806.tiff', '3']
['img_364.tiff', '3']
['img_65100.tiff', '3']
['img_27880.tiff', '3']
['img_3140.tiff', '3']
['img_8984.tiff', '3']
['img_26704.tiff', '3']
['img_44773.tiff', '3']
['img_49844.tiff', '3']
['img_19403.tiff', '3']
['img_22997.tiff', '3']
['img_7045.tiff', '3']
['img_65330.tiff', '3']
['img_79888.tiff', '3']
['img_33393.tiff', '3']
['img_18595.tiff', '3']
['img_35683.tiff', '3']
['img_19520.tiff', '3']
['img_41936.tiff', '3']
['img_20235.tiff', '3']
['img_45430.tiff', '3']
['img_79882.tiff', '3']
['img_61835.tiff', '3']
['img_38268.tiff', '3']
['img_65320.tiff', '3']
['img_53848.tiff', '3']
['img_20198.tiff', '3'

['img_21013.tiff', '3']
['img_43702.tiff', '3']
['img_41326.tiff', '3']
['img_3986.tiff', '3']
['img_898.tiff', '3']
['img_390.tiff', '3']
['img_38746.tiff', '3']
['img_7981.tiff', '3']
['img_46531.tiff', '3']
['img_69789.tiff', '3']
['img_83989.tiff', '3']
['img_78784.tiff', '3']
['img_80155.tiff', '3']
['img_7849.tiff', '3']
['img_73363.tiff', '3']
['img_19126.tiff', '3']
['img_18452.tiff', '3']
['img_18312.tiff', '3']
['img_7057.tiff', '3']
['img_36682.tiff', '3']
['img_19826.tiff', '3']
['img_3923.tiff', '3']
['img_80356.tiff', '3']
['img_25496.tiff', '3']
['img_39329.tiff', '3']
['img_58235.tiff', '3']
['img_69912.tiff', '3']
['img_10665.tiff', '3']
['img_20293.tiff', '3']
['img_85743.tiff', '3']
['img_76645.tiff', '3']
['img_53097.tiff', '3']
['img_68983.tiff', '3']
['img_36136.tiff', '3']
['img_51338.tiff', '3']
['img_78644.tiff', '3']
['img_19042.tiff', '3']
['img_28378.tiff', '3']
['img_8047.tiff', '3']
['img_84698.tiff', '3']
['img_58354.tiff', '3']
['img_6899.tiff', '3']
['i

In [165]:
with open('label.csv') as a:
    reader=csv.reader(a)
    i=0
    for row in reader:
        if i==10:
            break
        print(row)
        i=i+1

['img_13061.tiff', '1']
['img_19104.tiff', '1']
['img_22738.tiff', '1']
['img_84618.tiff', '1']
['img_33129.tiff', '1']
['img_34315.tiff', '1']
['img_30460.tiff', '1']
['img_84896.tiff', '1']
['img_66906.tiff', '1']
['img_42995.tiff', '1']
